Graph convolutional network for fMRI analysis based on connectivity neighborhood:
The paper outlines a methodology for converting functional connectivity (FC) matrices from fMRI data into graph structures using a k-nearest neighbors (k-NN) approach. The k-NN graph is built by connecting each node (ROI) to its k nearest neighbors based on the strength of connectivity, which is represented by the FC matrix values.

In [12]:
import nibabel as nib
import numpy as np
import networkx as nx
import os
import math
import pandas as pd
from tqdm.notebook import tqdm  # Import tqdm for notebooks
import matplotlib.pyplot as plt
import subprocess
#import utils


In [39]:
def load_fc_matrix(file_path):
    """ Load functional connectivity matrix from a .pconn.nii file. """
    img = nib.load(file_path)
    fc_matrix = img.get_fdata()
    return fc_matrix

def create_knn_graph(fc_matrix, k=5):
    """ Create a graph from a functional connectivity matrix using k-nearest neighbors based on absolute values. """
    n = fc_matrix.shape[0]  # Number of nodes
    G = nx.Graph()
    for i in range(n):
        G.add_node(i)
    
    # For each node, add edges to the k-nearest neighbors based on absolute values of connectivity strengths
    for i in range(n):
        # Sort indices based on the absolute values, get the k highest values indices for each row
        indices = np.argsort(np.abs(fc_matrix[i]))[-k:]
        for j in indices:
            if i != j:  # Ensure no self-loops
                G.add_edge(i, j, weight=fc_matrix[i][j])
    
    return G
def create_threshold_graph(fc_matrix, std_multiplier=2):
    """
    Create a graph from a functional connectivity matrix by adding edges where the 
    absolute connection strength is above a threshold defined as a multiple of the
    standard deviation of the absolute values in the connectivity matrix.
    """
    n = fc_matrix.shape[0]  # Number of nodes
    G = nx.Graph()
    
    # Calculate the threshold as std_multiplier times the standard deviation of the absolute values
    threshold = std_multiplier * np.std(np.abs(fc_matrix))
    
    # Add nodes
    for i in range(n):
        G.add_node(i)
    
    # Add edges based on the threshold
    for i in range(n):
        for j in range(n):
            if i != j and np.abs(fc_matrix[i, j]) > threshold:  # Avoid self-loops and check threshold
                G.add_edge(i, j, weight=fc_matrix[i, j])
    
    return G

In [3]:
# Directory containing the pconn files
directory = "C:/Users/manfr/OneDrive/Escritorio/Manfred/EMAI/SecondSemester_Slovenia/Project/BSNIP_neural/BSNIP/pconn"
pconn_files = [f for f in os.listdir(directory) if f.endswith('.pconn.nii')]

# Prepare a list to store the results
results = []

for file_name in tqdm(pconn_files, desc="Processing .pconn.nii files"):
    fc_file_path = os.path.join(directory, file_name)
    fc_matrix = load_fc_matrix(fc_file_path)
    graph = create_knn_graph(fc_matrix, k=5)

    degrees = [deg for _, deg in graph.degree()]
    n = graph.number_of_nodes()
    if n > 1:  # To avoid division by zero in calculations
        average_degree = sum(degrees) / n
        theoretical_avg_c = average_degree / (n - 1)
        theoretical_avg_d = math.log(n) / math.log(average_degree) if average_degree > 1 else 0

        # Calculate clustering and path length on the largest connected component
        largest_cc = max(nx.connected_components(graph), key=len)
        subgraph = graph.subgraph(largest_cc)
        size_of_largest_cc = len(largest_cc)
        avg_clustering = nx.average_clustering(graph)
        avg_path_length = nx.average_shortest_path_length(subgraph) if len(largest_cc) > 1 else 0

        row = [
            file_name, n, average_degree, theoretical_avg_c, avg_clustering,
            theoretical_avg_d, avg_path_length, math.log(n), math.log(math.log(n)),
            size_of_largest_cc
        ]
    else:
        row = [file_name, n, 0, 0, 0, 0, 0, 0, 0, 0]

    results.append(row)
# Create a DataFrame
df = pd.DataFrame(results, columns=[
    'File Name', 'Number of Nodes', 'Average Degree', 'Theoretical Avg Clustering',
    'Average Clustering', 'Theoretical Avg Path Length', 'Average Path Length',
    'Log of Nodes', 'Log Log of Nodes', 'Size of Largest CC'
])

# Save to CSV
df.to_csv('graph_statistics.csv', index=False)
print("Data saved to 'graph_statistics.csv'.")


FileNotFoundError: [Errno 2] No such file or directory: 'C:/Users/manfr/OneDrive/Escritorio/Manfred/EMAI/SecondSemester_Slovenia/Project/BSNIP_neural/BSNIP/pconn'

In [59]:
import os
import matplotlib.pyplot as plt


def plot(G, orbits):
    fig, axes = plt.subplots(3, 5)
    fig.suptitle(G.name)

    for o in range(15):
        nk = {}
        for i in range(len(G)):
            k = orbits[i][o]
            if k not in nk:
                nk[k] = 0
            nk[k] += 1
        ks = sorted(nk.keys())

        axes[o // 5, o % 5].loglog(ks, [nk[k] / len(G)
                                   for k in ks], 'ok', markersize=1)
        axes[o // 5, o % 5].set_xticks([])
        axes[o // 5, o % 5].set_yticks([])

    plt.savefig(G.name + ".png", bbox_inches='tight')
    plt.close()


def orca(G, exe_folder=".", output_folder="."):
    orca_executable = os.path.join(exe_folder, 'orca')
    if not os.path.isfile(orca_executable):
        raise Exception(f"{orca_executable} does not exist or is not a file")
    
    input_file = os.path.join(output_folder, f"{G.name}.in")
    output_file = os.path.join(output_folder, f"{G.name}.orca")
    
    # Write the graph to the input file
    with open(input_file, 'w') as file:
        file.write(f"{G.number_of_nodes()} {G.number_of_edges()}\n")
        for i, j in G.edges():
            file.write(f"{i} {j}\n")

    # Building the command
    command = [orca_executable, "node", "5", input_file, output_file]

    # Running the command
    try:
        result = subprocess.run(command, stdout=subprocess.PIPE, stderr=subprocess.PIPE, text=True, check=True)
        print("ORCA ran successfully:", result.stdout)
    except subprocess.CalledProcessError as e:
        print(f"Error running ORCA: {e.stderr}")
        return []

    # Read the output file and parse orbits
    orbits = []
    with open(output_file, 'r') as file:
        for line in file:
            orbits.append([int(k) for k in line.split()])

    return orbits

def calculate_agreement(orbits1, orbits2):
    # Ensure the orbit counts are in numpy arrays for easier manipulation
    orbits1 = np.array(orbits1, dtype=float)
    orbits2 = np.array(orbits2, dtype=float)

    # Avoid log of zero by replacing zero values with a small number
    orbits1[orbits1 == 0] = 1e-10
    orbits2[orbits2 == 0] = 1e-10

    # Calculate the logarithm of orbit frequencies
    log_orbits1 = np.log(orbits1)
    log_orbits2 = np.log(orbits2)

    # Calculate orbit agreement Ai for each orbit type
    Ai = 1 - np.sqrt(0.5 * np.sum((log_orbits1 - log_orbits2)**2, axis=1))
    # Make sure Ai does not contain invalid values for the geometric mean
    Ai[Ai <= 0] = 1e-10  # Replace non-positive values with a small positive number
    # Arithmetic and geometric means of Ai
    A_arithmetic = np.mean(Ai)
    A_geometric = np.prod(np.power(Ai, 1/len(Ai)))

    return A_arithmetic, A_geometric
def get_orbits(file_name):
    file_extension = '.pconn.nii'
    fc_file_path = os.path.join(directory, file_name+file_extension)
    fc_matrix = load_fc_matrix(fc_file_path)
    #graph = create_knn_graph(fc_matrix, k=5)
    graph = create_threshold_graph(fc_matrix,std_multiplier=4.5)
    graph.name = file_name  # Ensure the graph has a name attribute
    # Usage example
    exe_folder = '/home/tico/Desktop/master_classes/project/orca'
    output_folder = '/home/tico/Desktop/master_classes/project/output'
    orbits = orca(graph, exe_folder, output_folder)
    return orbits

In [60]:
behavior_path = '/home/tico/Desktop/master_classes/project/behavior/'
behavior_files = os.listdir(behavior_path)

behavior_source = pd.read_csv(behavior_path+behavior_files[0], sep='\t')
for behavior_file in behavior_files[1:]:
    curr_behavior_source = pd.read_csv(behavior_path+behavior_file, sep='\t')
    behavior_source = pd.concat([behavior_source, curr_behavior_source], axis=0)
behavior_source = behavior_source[["session_id","Group"]]
behavior_source



directory = "/home/tico/Desktop/master_classes/project/BSNIP/pconn"
pconn_files = [f for f in os.listdir(directory) if f.endswith('.pconn.nii')]
print(len(pconn_files))
orbits = get_orbits(pconn_files[0][:-len('.pconn.nii')])
idx=1
fc_file_path2 = os.path.join(directory, pconn_files[idx])
fc_matrix2 = load_fc_matrix(fc_file_path2)
#graph2 = create_knn_graph(fc_matrix2, k=5)
graph2 = create_threshold_graph(fc_matrix2,std_multiplier=4.5)#
print(graph2.number_of_edges())
graph2.name = pconn_files[idx][:-len('.pconn.nii')]
orbits2 = orca(graph2, exe_folder, output_folder)
A_arithmetic, A_geometric = calculate_agreement(orbits, orbits2)
print("Arithmetic Agreement:", A_arithmetic)
print("Geometric Agreement:", A_geometric)

638
ORCA ran successfully: nodes: 718
edges: 1016
max degree: 20
Counting NODE orbits of graphlets on 5 nodes.

stage 1 - precomputing common nodes
0%
1%
2%
3%
4%
5%
6%
7%
8%
9%
10%
11%
12%
13%
14%
15%
16%
17%
18%
19%
20%
21%
22%
23%
24%
25%
26%
27%
28%
29%
30%
31%
32%
33%
34%
35%
36%
37%
38%
39%
40%
41%
42%
43%
44%
45%
46%
47%
48%
49%
50%
51%
52%
53%
54%
55%
56%
57%
58%
59%
60%
61%
62%
63%
64%
65%
66%
67%
68%
69%
70%
71%
72%
73%
74%
75%
76%
77%
78%
79%
80%
81%
82%
83%
84%
85%
86%
87%
88%
89%
90%
91%
92%
93%
94%
95%
96%
97%
98%
99%
0.00 sec
stage 2 - counting full graphlets
0%
1%
2%
3%
4%
5%
6%
7%
8%
9%
10%
11%
12%
13%
14%
15%
16%
17%
18%
19%
20%
21%
22%
23%
24%
25%
26%
27%
28%
29%
30%
31%
32%
33%
34%
35%
36%
37%
38%
39%
40%
41%
42%
43%
44%
45%
46%
47%
48%
49%
50%
51%
52%
53%
54%
55%
56%
57%
58%
59%
60%
61%
62%
63%
64%
65%
66%
67%
68%
69%
70%
71%
72%
73%
74%
75%
76%
77%
78%
79%
80%
81%
82%
83%
84%
85%
86%
87%
88%
89%
90%
91%
92%
93%
94%
95%
96%
97%
98%
99%
0.00 sec
stage 3 - building s

In [62]:
# Load all behavioral data and concatenate into a single DataFrame
behavior_files = os.listdir('/home/tico/Desktop/master_classes/project/behavior/')
behavior_data = [pd.read_csv(f'/home/tico/Desktop/master_classes/project/behavior/{f}', sep='\t') for f in behavior_files]
behavior_source = pd.concat(behavior_data)
behavior_source = behavior_source[['session_id', 'Group']]

# Sample 20% of session IDs from each group
sampled_sessions = behavior_source.groupby('Group').apply(lambda x: x.sample(frac=0.2))
# Reset index after sampling if 'Group' is part of the index
sampled_sessions = sampled_sessions.reset_index(drop=True)
sampled_sessions

/tmp/ipykernel_2301335/3841553112.py:8: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  sampled_sessions = behavior_source.groupby('Group').apply(lambda x: x.sample(frac=0.2))


session_id Group
0    S1295TEN1   BPP
1    S8576HUL1   BPP
2    S4252XTK1   BPP
3    S5256LMQ1   BPP
4    S6176LLP1   BPP
..         ...   ...
122  S9764NJF1  SCZP
123  S2910BTW1  SCZP
124  S3895VIF1  SCZP
125  S1653KEM1  SCZP
126  S0083CHN1  SCZP

[127 rows x 2 columns]

In [63]:
from itertools import combinations

# Assuming orbits_data is a dictionary storing orbits with session_id as keys
# First, we calculate the agreements within and between groups
results = {group: [] for group in behavior_source['Group'].unique()}
agreements = pd.DataFrame(0, index=behavior_source['Group'].unique(), columns=behavior_source['Group'].unique())

# Calculate within and between group agreements
for (group1, sessions1), (group2, sessions2) in combinations(sampled_sessions.groupby('Group'), 2):
    for session1 in sessions1['session_id']:
        for session2 in sessions2['session_id']:
            orb1 = get_orbits(session1)
            orb2 = get_orbits(session2)
            A_arithmetic, A_geometric = calculate_agreement(orb1, orb2)
            agreements.at[group1, group2] += A_arithmetic
            agreements.at[group2, group1] += A_geometric

# Normalize the results to get the average agreements
for group in agreements.columns:
    total_sessions = len(sampled_sessions[sampled_sessions['Group'] == group])
    agreements[group] /= total_sessions

ORCA ran successfully: nodes: 718
edges: 14
max degree: 2
Counting NODE orbits of graphlets on 5 nodes.

stage 1 - precomputing common nodes
0%
1%
2%
3%
4%
5%
6%
7%
8%
9%
10%
11%
12%
13%
14%
15%
16%
17%
18%
19%
20%
21%
22%
23%
24%
25%
26%
27%
28%
29%
30%
31%
32%
33%
34%
35%
36%
37%
38%
39%
40%
41%
42%
43%
44%
45%
46%
47%
48%
49%
50%
51%
52%
53%
54%
55%
56%
57%
58%
59%
60%
61%
62%
63%
64%
65%
66%
67%
68%
69%
70%
71%
72%
73%
74%
75%
76%
77%
78%
79%
80%
81%
82%
83%
84%
85%
86%
87%
88%
89%
90%
91%
92%
93%
94%
95%
96%
97%
98%
99%
0.00 sec
stage 2 - counting full graphlets
0%
1%
2%
3%
4%
5%
6%
7%
8%
9%
10%
11%
12%
13%
14%
15%
16%
17%
18%
19%
20%
21%
22%
23%
24%
25%
26%
27%
28%
29%
30%
31%
32%
33%
34%
35%
36%
37%
38%
39%
40%
41%
42%
43%
44%
45%
46%
47%
48%
49%
50%
51%
52%
53%
54%
55%
56%
57%
58%
59%
60%
61%
62%
63%
64%
65%
66%
67%
68%
69%
70%
71%
72%
73%
74%
75%
76%
77%
78%
79%
80%
81%
82%
83%
84%
85%
86%
87%
88%
89%
90%
91%
92%
93%
94%
95%
96%
97%
98%
99%
0.00 sec
stage 3 - building systems 

/tmp/ipykernel_2301335/1171749037.py:15: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.9679665738193594' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  agreements.at[group1, group2] += A_arithmetic
/tmp/ipykernel_2301335/1171749037.py:16: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.478261848588381' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  agreements.at[group2, group1] += A_geometric


ORCA ran successfully: nodes: 718
edges: 14
max degree: 2
Counting NODE orbits of graphlets on 5 nodes.

stage 1 - precomputing common nodes
0%
1%
2%
3%
4%
5%
6%
7%
8%
9%
10%
11%
12%
13%
14%
15%
16%
17%
18%
19%
20%
21%
22%
23%
24%
25%
26%
27%
28%
29%
30%
31%
32%
33%
34%
35%
36%
37%
38%
39%
40%
41%
42%
43%
44%
45%
46%
47%
48%
49%
50%
51%
52%
53%
54%
55%
56%
57%
58%
59%
60%
61%
62%
63%
64%
65%
66%
67%
68%
69%
70%
71%
72%
73%
74%
75%
76%
77%
78%
79%
80%
81%
82%
83%
84%
85%
86%
87%
88%
89%
90%
91%
92%
93%
94%
95%
96%
97%
98%
99%
0.00 sec
stage 2 - counting full graphlets
0%
1%
2%
3%
4%
5%
6%
7%
8%
9%
10%
11%
12%
13%
14%
15%
16%
17%
18%
19%
20%
21%
22%
23%
24%
25%
26%
27%
28%
29%
30%
31%
32%
33%
34%
35%
36%
37%
38%
39%
40%
41%
42%
43%
44%
45%
46%
47%
48%
49%
50%
51%
52%
53%
54%
55%
56%
57%
58%
59%
60%
61%
62%
63%
64%
65%
66%
67%
68%
69%
70%
71%
72%
73%
74%
75%
76%
77%
78%
79%
80%
81%
82%
83%
84%
85%
86%
87%
88%
89%
90%
91%
92%
93%
94%
95%
96%
97%
98%
99%
0.00 sec
stage 3 - building systems 

In [ ]:
# DataFrames to hold the average arithmetic and geometric agreements
average_arithmetic = agreements.copy()
average_geometric = agreements.copy()

# Assuming arithmetic and geometric results are stored differently, adjust the above calculations accordingly
# For example, if you stored them separately, you might have:
# average_arithmetic[group1][group2] = total_arithmetic_agreement / count_of_comparisons
# average_geometric[group1][group2] = total_geometric_agreement / count_of_comparisons

print(average_arithmetic)
print(average_geometric)

In [31]:
import os
import numpy as np
import matplotlib.pyplot as plt
from scipy.spatial.distance import pdist, squareform

def plot_agreements(agreements, title):
    arithmetic, geometric = zip(*agreements)
    plt.figure(figsize=(10, 5))
    plt.subplot(1, 2, 1)
    plt.scatter(arithmetic, geometric, c='blue')
    plt.title('Arithmetic vs. Geometric Agreement')
    plt.xlabel('Arithmetic Agreement')
    plt.ylabel('Geometric Agreement')
    plt.grid(True)

    plt.subplot(1, 2, 2)
    plt.hist(arithmetic, bins=20, alpha=0.7, label='Arithmetic')
    plt.hist(geometric, bins=20, alpha=0.7, label='Geometric')
    plt.title('Histogram of Agreements')
    plt.xlabel('Agreement Score')
    plt.ylabel('Frequency')
    plt.legend()
    plt.tight_layout()
    plt.show()

# Main execution block
directory = "/home/tico/Desktop/master_classes/project/BSNIP/pconn"
exe_folder = '/home/tico/Desktop/master_classes/project/orca'
output_folder = '/home/tico/Desktop/master_classes/project/output'
files = [os.path.join(directory, f) for f in os.listdir(directory) if f.endswith('.pconn.nii')]
orbits = {f: orca(create_knn_graph(load_fc_matrix(f), k=5), exe_folder, output_folder) for f in files}

# Calculate pairwise agreements
pairwise_agreements = []
for i in range(len(files)):
    for j in range(i + 1, len(files)):
        A_arithmetic, A_geometric = calculate_agreement(orbits[files[i]], orbits[files[j]])
        pairwise_agreements.append((A_arithmetic, A_geometric))

# Plot the results
plot_agreements(pairwise_agreements, "Graphlet Agreement Between Networks")

ORCA ran successfully: nodes: 718
edges: 2116
max degree: 18
Counting NODE orbits of graphlets on 5 nodes.

stage 1 - precomputing common nodes
0%
1%
2%
3%
4%
5%
6%
7%
8%
9%
10%
11%
12%
13%
14%
15%
16%
17%
18%
19%
20%
21%
22%
23%
24%
25%
26%
27%
28%
29%
30%
31%
32%
33%
34%
35%
36%
37%
38%
39%
40%
41%
42%
43%
44%
45%
46%
47%
48%
49%
50%
51%
52%
53%
54%
55%
56%
57%
58%
59%
60%
61%
62%
63%
64%
65%
66%
67%
68%
69%
70%
71%
72%
73%
74%
75%
76%
77%
78%
79%
80%
81%
82%
83%
84%
85%
86%
87%
88%
89%
90%
91%
92%
93%
94%
95%
96%
97%
98%
99%
0.00 sec
stage 2 - counting full graphlets
0%
1%
2%
3%
4%
5%
6%
7%
8%
9%
10%
11%
12%
13%
14%
15%
16%
17%
18%
19%
20%
21%
22%
23%
24%
25%
26%
27%
28%
29%
30%
31%
32%
33%
34%
35%
36%
37%
38%
39%
40%
41%
42%
43%
44%
45%
46%
47%
48%
49%
50%
51%
52%
53%
54%
55%
56%
57%
58%
59%
60%
61%
62%
63%
64%
65%
66%
67%
68%
69%
70%
71%
72%
73%
74%
75%
76%
77%
78%
79%
80%
81%
82%
83%
84%
85%
86%
87%
88%
89%
90%
91%
92%
93%
94%
95%
96%
97%
98%
99%
0.00 sec
stage 3 - building syste

KeyboardInterrupt: 

In [32]:
labels_df = pd.read_csv('/home/tico/Desktop/master_classes/project/BSNIP_data/neural/neural_parcellated_gbc.csv')
labels_df

Unnamed: 0 Group        X1        X2        X3        X4        X5  \
0             1  SADP  0.017901  0.009985  0.003740  0.012205  0.005254   
1             2  SCZP  0.006281  0.014014 -0.005585 -0.000536  0.003254   
2             3   BPP -0.011590  0.009900 -0.008592 -0.009722  0.001935   
3             4  SCZP  0.017341  0.009125  0.001433  0.005714  0.000891   
4             5  SADP -0.025011  0.031992 -0.037631 -0.024702 -0.009084   
..          ...   ...       ...       ...       ...       ...       ...   
633         634   CON -0.001586 -0.005334 -0.001277 -0.001446 -0.000922   
634         635   CON -0.003809 -0.008047 -0.004458 -0.003700 -0.002667   
635         636   CON -0.002485  0.003286  0.001534 -0.001186 -0.000659   
636         637   CON -0.000164 -0.000084  0.000133 -0.000045  0.000366   
637         638   CON  0.000647  0.000025  0.001216  0.000255 -0.000098   

           X6        X7        X8  ...      X709      X710      X711  \
0    0.023362  0.009241 -0.013089  ...  0.014800 -0.000650 -0.007422   
1    0.008885  0.008263 -0.007209  ... -0.002154  0.007586  0.004824   
2    0.016690  0.007919 -0.006034  ... -0.003193 -0.018124  0.012447   
3    0.004737  0.000913 -0.004097  ... -0.006566  0.018083  0.007969   
4   -0.002958  0.031740  0.018152  ... -0.004469  0.037608  0.032018   
..        ...       ...       ...  ...       ...       ...       ...   
633 -0.001493 -0.004710  0.005046  ... -0.008898  0.003685  0.010149   
634 -0.003373 -0.002219  0.002508  ...  0.006165  0.003133  0.003173   
635  0.000168  0.002753  0.006324  ...  0.000631 -0.008656  0.000707   
636  0.000364  0.000193  0.000473  ... -0.000565 -0.002743  0.001646   
637  0.000227 -0.000121  0.001089  ...  0.000225 -0.000304  0.001843   

         X712      X713      X714      X715      X716      X717      X718  
0   -0.003942  0.005397  0.000533  0.013678 -0.014425  0.000760  0.000889  
1    0.008781 -0.007612  0.005459  0.004697  0.002705  0.008613  0.005739  
2   -0.000854 -0.003363  0.001340 -0.007613  0.001474 -0.003668  0.005865  
3    0.005143  0.010550  0.000927  0.015112  0.003535  0.008583  0.006735  
4    0.005771  0.000471  0.017834  0.020844  0.039692  0.029756  0.003653  
..        ...       ...       ...       ...       ...       ...       ...  
633  0.009024 -0.002084  0.004841  0.004243  0.006039  0.000987  0.010931  
634  0.004820 -0.005138  0.001226 -0.002321  0.005364 -0.001979 -0.003046  
635 -0.001676  0.011075 -0.003262 -0.002351 -0.006942 -0.005176 -0.004017  
636  0.001247  0.001187  0.002194  0.000646  0.000297 -0.001293  0.000537  
637  0.000907  0.001322  0.000198 -0.000922  0.000063 -0.000672  0.000249  

[638 rows x 720 columns]